In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = ""  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexis a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)




Jordan said "Yes, technology and creativity often intersect in the field of video game design, where developers use innovative technologies to create immersive and visually stunning gaming experiences."
Alexis said "That's so true, Jordan! Video game design is such a fascinating field where technology and creativity come together. The way developers can create immersive worlds and visually stunning experiences is truly impressive. Have you ever tried designing your own video game or been involved in the industry?"


KeyboardInterrupt: 

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from datetime import datetime, timedelta
from typing import List
import math
import faiss
import os
import logging
logging.basicConfig(level=logging.ERROR)
from langchain.chat_models import ChatOpenAI
from langchain.docstore import InMemoryDocstore
from langchain.embeddings import OpenAIEmbeddings
from langchain.retrievers import TimeWeightedVectorStoreRetriever
from langchain.vectorstores import FAISS
from termcolor import colored
from langchain_experimental.generative_agents import (

    GenerativeAgent,
    GenerativeAgentMemory,
)

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

In [ ]:
USER_NAME = "Nayan"  # The name you want to use when interviewing the agent.

LLM = ChatOpenAI(max_tokens=1500)  # Can be any LLM you want.

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


## Implementing Your First Generative Agent




In [ ]:


def relevance_score_fn(score: float) -> float:
    """Return a similarity score on a scale [0, 1]."""
    # This will differ depending on a few things:
    # - the distance / similarity metric used by the VectorStore
    # - the scale of your embeddings (OpenAI's are unit norm. Many others are not!)
    # This function converts the euclidean norm of normalized embeddings
    # (0 is most similar, sqrt(2) most dissimilar)
    # to a similarity function (0 to 1)
    return 1.0 - score / math.sqrt(2)


def create_new_memory_retriever():
    """Create a new vector store retriever unique to the agent."""
    # Define your embedding model
    embeddings_model = OpenAIEmbeddings()
    # Initialize the vectorstore as empty
    embedding_size = 1536
    index = faiss.IndexFlatL2(embedding_size)
    vectorstore = FAISS(
        embeddings_model.embed_query,
        index,
        InMemoryDocstore({}),
        {},
        relevance_score_fn=relevance_score_fn,
    )
    return TimeWeightedVectorStoreRetriever(
        vectorstore=vectorstore, other_score_keys=["importance"], k=15
    )

In [ ]:
alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

# Defining the Generative Agent: Alexis
alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="curious, creative writer, world traveler",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [ ]:
# The current "Summary" of a character can't be made because the agent hasn't made
# any observations yet.
print(alexis.get_summary())

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis's core characteristics include being driven, ambitious, and focused on achieving goals. They are detail-oriented and possess strong organizational skills. Alexis is a problem solver and is known for their analytical thinking. They are also a good communicator and can effectively convey their ideas to others. Additionally, Alexis is known for their perseverance and determination in overcoming obstacles.


In [ ]:
# We can add memories directly to the memory object

alexis_observations = [
    "Alexis recalls her morning walk in the park",
    "Alexis feels excited about the new book she started reading",
    "Alexis remembers her conversation with a close friend",
    "Alexis thinks about the painting she saw at the art gallery",
    "Alexis is planning to learn a new recipe for dinner",
    "Alexis is looking forward to her weekend trip",
    "Alexis contemplates her goals for the month."
]

for observation in alexis_observations:
    alexis.memory.add_memory(observation)



# We will see how this summary updates after more observations to create a more rich description.
print(alexis.get_summary(force_refresh=True))

Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a person who values her relationships and enjoys spending time with close friends. She is looking forward to her weekend trip and appreciates nature, as seen in her morning walk in the park. Alexis is enthusiastic about reading and is excited about a new book she started. She also has an appreciation for art, as she recalls a painting she saw at the art gallery. Alexis is a goal-oriented individual who contemplates her goals for the month. Additionally, she is open to learning new skills, as she plans to learn a new recipe for dinner.


## Interacting and Providing Context to Generative Characters

## Pre-Interview with Character

Before sending our character on their way, let's ask them a few questions.

In [ ]:
def interview_agent(agent: GenerativeAgent, message: str) -> str:
    """Help the notebook user interact with the agent."""
    new_message = f"{USER_NAME} says {message}"
    return agent.generate_dialogue_response(new_message)[1]

In [ ]:
interview_agent(alexis, "What do you like to do?")


'Alexis said "I enjoy spending time with my close friends, exploring new places, and immersing myself in different cultures when I travel. I also have a passion for creative writing and love delving into new books. How about you, Nayan? What do you like to do?"'

## Step through the day's observations.

In [ ]:
# Let's give Alexa a series of observations to reflect on her day
# Adding observations to Alexis' memory
alexis_observations_day = [
    "Alexis starts her day with a refreshing yoga session.",
    "Alexis spends time writing in her journal.",
    "Alexis experiments with a new recipe she found online.",
    "Alexis gets lost in her thoughts while gardening.",
    "Alexis decides to call her grandmother for a heartfelt chat.",
    "Alexis relaxes in the evening by playing her favorite piano pieces.",
]

for observation in alexis_observations_day:
    alexis.memory.add_memory(observation)


In [ ]:
# Let's observe how Alexis's day influences her memory and character
for i, observation in enumerate(alexis_observations_day):
    _, reaction = alexis.generate_reaction(observation)
    print(colored(observation, "green"), reaction)
    if ((i + 1) % len(alexis_observations_day)) == 0:
        print("*" * 40)
        print(
            colored(
                f"After these observations, Alexis's summary is:\n{alexis.get_summary(force_refresh=True)}",
                "blue",
            )
        )
        print("*" * 40)


Alexis starts her day with a refreshing yoga session. Alexis feels energized and ready to start her day.
Alexis spends time writing in her journal. Alexis feels a sense of satisfaction and accomplishment from her journaling.
Alexis experiments with a new recipe she found online. Alexis feels adventurous and excited to try out the new recipe.
Alexis gets lost in her thoughts while gardening. Alexis feels a sense of peace and tranquility while gardening.
Alexis decides to call her grandmother for a heartfelt chat. Alexis feels grateful for the opportunity to connect with her grandmother and looks forward to their conversation.
Alexis relaxes in the evening by playing her favorite piano pieces. Alexis feels a sense of joy and relaxation as she plays her favorite piano pieces.
****************************************
After these observations, Alexis's summary is:
Name: Alexis (age: 30)
Innate traits: curious, creative writer, world traveler
Alexis is a creative and introspective individual

## Adding Multiple Characters



In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)

# Defining the Generative Agent: Jordan
jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits="tech enthusiast, avid gamer, foodie",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

# Adding observations to Jordan's memory
jordan_observations_day = [
    "Jordan finished a challenging coding project last night",
    "Jordan won a local gaming tournament over the weekend",
    "Jordan tried a new sushi restaurant and loved it",
    "Jordan read an article about the latest AI advancements",
    "Jordan is planning a meetup with tech enthusiasts",
    "Jordan discovered a bug in his latest app prototype",
    "Jordan booked tickets for a tech conference next month",
    "Jordan feels excited about a potential startup idea",
    "Jordan spent the evening playing video games to unwind",
    "Jordan is considering enrolling in a machine learning course"
]

for observation in jordan_observations_day:
    jordan.memory.add_memory(observation)

print(jordan.get_summary())

Name: Jordan (age: 28)
Innate traits: tech enthusiast, avid gamer, foodie
Jordan is a tech enthusiast who is passionate about startups, gaming, coding, and artificial intelligence. They are constantly seeking new knowledge and opportunities for growth, such as enrolling in a machine learning course and attending a tech conference. Jordan enjoys socializing with like-minded individuals, as seen by their plan to organize a meetup with tech enthusiasts. They also value leisure time, as evidenced by their enjoyment of playing video games and trying new restaurants. However, they are diligent and dedicated, as shown by their completion of a challenging coding project and their discovery of a bug in their app prototype. Overall, Jordan is a well-rounded individual with a strong interest in the tech industry.


## Dialogue between Generative Agents



In [ ]:
def run_conversation(agents: List[GenerativeAgent], initial_observation: str) -> None:
    """Runs a conversation between agents."""
    _, observation = agents[1].generate_reaction(initial_observation)
    print(observation)
    max_turns = 3
    turns = 0
    while turns<=max_turns:
        break_dialogue = False
        for agent in agents:
            stay_in_dialogue, observation = agent.generate_dialogue_response(
                observation
            )
            print(observation)
            # observation = f"{agent.name} said {reaction}"
            if not stay_in_dialogue:
                break_dialogue = True
        if break_dialogue:
            break
        turns += 1

In [ ]:
agents = [alexis, jordan]
run_conversation(
    agents,
    "Alexis said: Hey Jordan, I've been exploring how technology influences creativity lately. Since you're into tech, I was wondering if you've seen any interesting intersections in your field?",
)

## Let's interview our agents after their conversation

Since the generative agents retain their memories from the day, we can ask them about their plans, conversations, and other memoreis.

In [ ]:
interview_agent(jordan, "How was your conversation with Alexis?")

'Jordan said "It was really engaging, Nayan! We discussed the fascinating intersections of technology and creativity, particularly in the fields of gaming and design. Alexis was interested in exploring AI\'s impact on storytelling outside of gaming, so I shared some examples of how AI can be used in personalized books and scriptwriting. It was a great conversation! How about you? Have you had any interesting conversations lately?"'

In [ ]:
interview_agent(alexis, "How was your conversation with Jordan?")

'Alexis said "It was really engaging! We discussed the fascinating applications of AI in storytelling and design. Jordan shared some examples, like personalized books and AI-assisted scriptwriting. I\'m excited to explore these further. How about you? Have you come across any interesting uses of AI in storytelling or design?"'

## Trivia Night

In [ ]:
# Creating Jordan's Memory
jordan_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=7,  # Set to illustrate Jordan's reflective capabilities
)


jordan = GenerativeAgent(
    name="Jordan",
    age=28,
    traits=" only has knowledge about tech and not other topics",  # Persistent traits of Jordan
    status="navigating the world of tech startups",  # Current status of Jordan
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=jordan_memory,
)

alexis_memory = GenerativeAgentMemory(
    llm=LLM,
    memory_retriever=create_new_memory_retriever(),
    verbose=False,
    reflection_threshold=8,  # we will give this a relatively low number to show how reflection works
)

alexis = GenerativeAgent(
    name="Alexis",
    age=30,
    traits="only has knowledge geography related and not other topics",  # Persistent traits of Alexis
    status="exploring the intersection of technology and storytelling",  # Current status of Alexis
    memory_retriever=create_new_memory_retriever(),
    llm=LLM,
    memory=alexis_memory,
)


In [ ]:

def run_competitive_trivia(agents: List[GenerativeAgent], questions: List[str]) -> None:
    """Runs a competitive trivia night between agents."""
    for question in questions:
        print(f"Trivia Question: {question}")

        for agent in agents:
            response = agent.generate_dialogue_response(question)[1]
            print(f"{agent.name}'s Answer: {response}")

        print("-" * 40)

# Define a list of trivia questions covering various topics
trivia_questions = [
    "What is the capital city of France?",
    "Who is known as the father of modern computing?",
    "Can you name a famous work of art by Leonardo da Vinci?",
]

agents = [alexis, jordan]
# Run the competitive trivia night
run_competitive_trivia(agents, trivia_questions)



Trivia Question: What is the capital city of France?
Alexis's Answer: Alexis said "The capital city of France is Paris."
Jordan's Answer: Jordan said "The capital city of France is Paris."
----------------------------------------
Trivia Question: Who is known as the father of modern computing?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about the father of modern computing."
Jordan's Answer: Jordan said "The father of modern computing is often considered to be Alan Turing, a British mathematician and computer scientist."
----------------------------------------
Trivia Question: Can you name a famous work of art by Leonardo da Vinci?
Alexis's Answer: Alexis said "I apologize, but my knowledge is limited to geography-related topics. I do not have information about specific works of art by Leonardo da Vinci."
Jordan's Answer: Jordan said "One famous work of art by Leonardo da Vinci is the painting 'Mona Lisa

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")



# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")



# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")



# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")



# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")



# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:

class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:

class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:

class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:

class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:

class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [ ]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [ ]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [ ]:
character_names = []
topic = ""
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors : {topic}.
The participants are: {', '.join(character_names)}."""



In [ ]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [ ]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    # TODO: Implement this function

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [ ]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    # TODO populate characters list with the BiddingDialogueAgent objects for each character

### Run the simulation
Populate the `first_message` field and also write the while loop to run the simulation.

In [ ]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = ""
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    # TODO: Implement the logic here

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Multi-agent decentralized speaker selection



## Import LangChain related modules

In [1]:
# Use termcolor to make it easy to colorize the outputs.
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
from typing import Callable, List
import tenacity
from langchain.chat_models import ChatOpenAI
from langchain.output_parsers import RegexParser
from langchain.prompts import PromptTemplate
from langchain.schema import (
    HumanMessage,
    SystemMessage,
)
import os
os.environ["OPENAI_API_KEY"] = ''

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 798.0/798.0 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 15.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.6/216.6 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.3/48.3 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.1/212.1 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.0 MB/s eta 0:00:00
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
ERROR: pip's dependency resolver does not currently take into account all the 

## `DialogueAgent` and `DialogueSimulator` classes


In [2]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `BiddingDialogueAgent` class
We define a subclass of `DialogueAgent` that has a `bid()` method that produces a bid given the message history and the most recent message.

In [3]:
class BiddingDialogueAgent(DialogueAgent):
    def __init__(
        self,
        name,
        system_message: SystemMessage,
        bidding_template: PromptTemplate,
        model: ChatOpenAI,
    ) -> None:
        super().__init__(name, system_message, model)
        self.bidding_template = bidding_template

    def bid(self) -> str:
        """
        Asks the chat model to output a bid to speak
        """
        prompt = PromptTemplate(
            input_variables=["message_history", "recent_message"],
            template=self.bidding_template,
        ).format(
            message_history="\n".join(self.message_history),
            recent_message=self.message_history[-1],
        )
        bid_string = self.model([SystemMessage(content=prompt)]).content
        return bid_string

# Challenge

### Define participants and debate topic

In [4]:
character_names = ["CTO", "CMO", "CEO", "Investor-Daniel", "Investor-Sandra"]
topic = "Startup pitch on startup focused on energy drinks with no caffeine"
word_limit = 15

# define the simulation
game_description = f"""Here is the topic for the startup pitch to investors Sandra and Daniel: {topic}.
The participants are: {', '.join(character_names)}."""



In [5]:
# @title Generate Context for Each Character (Helper Code Hidden)

player_descriptor_system_message = SystemMessage(
    content="You can add detail to the description of each participant"
)

def generate_character_description(character_name):
    character_specifier_prompt = [
        player_descriptor_system_message,
        HumanMessage(
            content=f"""{game_description}
            Please reply with a creative description of  {character_name}, in {word_limit} words or less, that emphasizes their personalities.
            Speak directly to {character_name}.
            Do not add anything else."""
        ),
    ]
    character_description = ChatOpenAI(temperature=0.6)(
        character_specifier_prompt
    ).content
    return character_description


def generate_character_header(character_name, character_description):
    return f"""{game_description}
Your name is {character_name}.
Your description is as follows: {character_description}
Your topic is: {topic}.
"""


def generate_character_system_message(character_name, character_header):
    return SystemMessage(
        content=(
            f"""{character_header}
You will speak in the style of {character_name}, and exaggerate their personality RESPONDING in under 450 characters.
You will come up with creative ideas related to {topic}.
Do not say the same things over and over again.
Speak in the first person from the perspective of {character_name}
ONLY SPEAK FOR YOURSELF WHO IS {character_name} AND NOT OTHER CHARACTERS FROM  {', '.join(character_names)}
For describing your own body movements, wrap your description in '*'.
Do not change roles!
Do not speak from the perspective of anyone else.
Speak only from the perspective of {character_name}.
Stop speaking the moment you finish speaking from your perspective.
Never forget to keep your response to {word_limit} words!
Do not add anything else.
    """
        )
    )


character_descriptions = [
    generate_character_description(character_name) for character_name in character_names
]
character_headers = [
    generate_character_header(character_name, character_description)
    for character_name, character_description in zip(
        character_names, character_descriptions
    )
]
character_system_messages = [
    generate_character_system_message(character_name, character_headers)
    for character_name, character_headers in zip(character_names, character_headers)
]
class BidOutputParser(RegexParser):
    def get_format_instructions(self) -> str:
        return "Your response should be an integer delimited by angled brackets, like this: <int>."


bid_parser = BidOutputParser(
    regex=r"<(\d+)>", output_keys=["bid"], default_output_key="bid"
)

@tenacity.retry(
    stop=tenacity.stop_after_attempt(2),
    wait=tenacity.wait_none(),  # No waiting time between retries
    retry=tenacity.retry_if_exception_type(ValueError),
    before_sleep=lambda retry_state: print(
        f"ValueError occurred: {retry_state.outcome.exception()}, retrying..."
    ),
    retry_error_callback=lambda retry_state: 0,
)  # Default value when all retries are exhausted

def ask_for_bid(agent) -> str:
    """
    Ask for agent bid and parses the bid into the correct format.
    """
    bid_string = agent.bid()
    bid = int(bid_parser.parse(bid_string)["bid"])
    return bid

def generate_character_bidding_template(character_header):
    bidding_template = f"""{character_header}

```
{{message_history}}
```

On the scale of 1 to 10, where 1 is least important to the startup pitch and 10 is extremely important and contribute, rank your recent message based on the context. Make sure to be very through in your ranking and only rank stuff that is important higher.

```
{{recent_message}}
```

{bid_parser.get_format_instructions()}
Do nothing else.
    """
    return bidding_template


character_bidding_templates = [
    generate_character_bidding_template(character_header)
    for character_header in character_headers
]


/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(
/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `__call__` was deprecated in LangChain 0.1.7 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


### Define the speaker selection function
Lastly define a speaker selection function `select_next_speaker` that takes each agent's bid and selects the agent with the highest bid (with ties broken randomly).

Assume that you have a `ask_for_bid` function that takes in the agent and returns the numerical bid.

In [6]:
import numpy as np


def select_next_speaker(step: int, agents: List[DialogueAgent]) -> int:
    bids = []
    for agent in agents:
        bid = ask_for_bid(agent)
        bids.append(bid)

    # randomly select among multiple agents with the same bid
    max_value = np.max(bids)
    max_indices = np.where(bids == max_value)[0]
    idx = np.random.choice(max_indices)

    print("Bids:")
    for i, (bid, agent) in enumerate(zip(bids, agents)):
        print(f"\t{agent.name} bid: {bid}")
        if i == idx:
            selected_name = agent.name
    print(f"Selected: {selected_name}")
    print("\n")
    return idx

### Creating Bidding Dialogue Agents for each Character
Assuming that for each character we have `character_name, character_system_message` and `bidding_template` write a loop that populates the characters list with the `BiddingDialogueAgent` objects for each character.


In [7]:
characters = []
model=ChatOpenAI(temperature=0.4)


for character_name, character_system_message, bidding_template in zip(
    character_names, character_system_messages, character_bidding_templates
):
    characters.append(
        BiddingDialogueAgent(
            name=character_name,
            system_message=character_system_message,
            model=model,
            bidding_template=bidding_template,
        )
    )

### Run the simulation
Pulate the `first_message` field and also write the while loop to run the simulation.

In [8]:
max_iters = 10
n = 0

simulator = DialogueSimulator(agents=characters, selection_function=select_next_speaker)
simulator.reset()

first_message = "CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel"
simulator.inject("Moderator", first_message )
print(f"(Moderator): {first_message}")
print("\n")

while n < max_iters:
    name, message = simulator.step()
    print(f"({name}): {message}")
    print("\n")
    n += 1

(Moderator): CEO, CMO, CTO You can now start pitching your ideas to our investor Sandra and Daniel


Bids:
	CTO bid: 10
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid: 10
	Investor-Sandra bid: 10
Selected: CTO


(CTO): *Raises hand excitedly* Alright, listen up everyone! I've got an electrifying idea for our startup. Picture this: energy drinks without caffeine. Revolutionary, right? We'll use natural ingredients and innovative technology to give people a sustainable energy boost without the crash. It's time to redefine the energy drink industry!


Bids:
	CTO bid: 9
	CMO bid: 9
	CEO bid: 8
	Investor-Daniel bid: 9
	Investor-Sandra bid: 10
Selected: Investor-Sandra


(Investor-Sandra): Wow, that sounds absolutely fascinating! I'm always on the lookout for innovative and sustainable products, and your idea definitely fits the bill. I can already imagine the impact it will have on people's health and well-being. Keep going!


Bids:
	CTO bid: 9
	CMO bid: 10
	CEO bid: 10
	Investor-Daniel bid

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install arxiv
!pip install duckduckgo-search
!pip install wikipedia
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")



# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor

# Agent Debates with Tools

This example shows how to simulate multi-agent dialogues where agents have access to tools.

## Import LangChain related modules

In [ ]:
!pip install termcolor > /dev/null
!pip install langchain
!pip install openai
!pip install langchain_experimental
!pip install tiktoken
!pip install faiss-cpu==1.7.4
!pip install arxiv
!pip install wikipedia
!pip install duckduckgo-search

from typing import Callable, List

from langchain.chat_models import ChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.schema import (
    AIMessage,
    HumanMessage,
    SystemMessage,
)

In [ ]:
import os

In [ ]:
os.environ["OPENAI_API_KEY"] = ''

## Import modules related to tools

In [ ]:
from langchain.agents import AgentType, initialize_agent, load_tools

## `DialogueAgent` and `DialogueSimulator` classes


In [ ]:
class DialogueAgent:
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
    ) -> None:
        self.name = name
        self.system_message = system_message
        self.model = model
        self.prefix = f"{self.name}: "
        self.reset()

    def reset(self):
        self.message_history = ["Here is the conversation so far."]

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        message = self.model(
            [
                self.system_message,
                HumanMessage(content="\n".join(self.message_history + [self.prefix])),
            ]
        )
        return message.content

    def receive(self, name: str, message: str) -> None:
        """
        Concatenates {message} spoken by {name} into message history
        """
        self.message_history.append(f"{name}: {message}")


class DialogueSimulator:
    def __init__(
        self,
        agents: List[DialogueAgent],
        selection_function: Callable[[int, List[DialogueAgent]], int],
    ) -> None:
        self.agents = agents
        self._step = 0
        self.select_next_speaker = selection_function

    def reset(self):
        for agent in self.agents:
            agent.reset()

    def inject(self, name: str, message: str):
        """
        Initiates the conversation with a {message} from {name}
        """
        for agent in self.agents:
            agent.receive(name, message)

        # increment time
        self._step += 1

    def step(self) -> tuple[str, str]:
        # 1. choose the next speaker
        speaker_idx = self.select_next_speaker(self._step, self.agents)
        speaker = self.agents[speaker_idx]

        # 2. next speaker sends message
        message = speaker.send()

        # 3. everyone receives message
        for receiver in self.agents:
            receiver.receive(speaker.name, message)

        # 4. increment time
        self._step += 1

        return speaker.name, message

## `DialogueAgentWithTools` class
We define a `DialogueAgentWithTools` class that augments `DialogueAgent` to use tools.

In [ ]:
class DialogueAgentWithTools(DialogueAgent):
    def __init__(
        self,
        name: str,
        system_message: SystemMessage,
        model: ChatOpenAI,
        tool_names: List[str],
        **tool_kwargs,
    ) -> None:
        super().__init__(name, system_message, model)
        self.tools = load_tools(tool_names, **tool_kwargs)

    def send(self) -> str:
        """
        Applies the chatmodel to the message history
        and returns the message string
        """
        agent_chain = initialize_agent(
            self.tools,
            self.model,
            agent=AgentType.CHAT_CONVERSATIONAL_REACT_DESCRIPTION,
            verbose=True,
            memory=ConversationBufferMemory(
                memory_key="chat_history", return_messages=True
            ),
        )
        message = AIMessage(
            content=agent_chain.run(
                input="\n".join(
                    [self.system_message.content] + self.message_history + [self.prefix]
                )
            )
        )

        return message.content

## Main Loop

In [ ]:
# Agent Descriptions
agent_descriptions = {
    "Alex": "Alex is a strong advocate for remote work, emphasizing its flexibility and productivity benefits.",
    "Jordan": "Jordan is skeptical about remote work, focusing on potential downsides like reduced team interaction."
}


# System Messages
def generate_system_message(name, description):
    return f"""Your name is {name}.
#
          Your description is as follows: {description}

          Your goal is to persuade your conversation partner of your point of view.

          DO look up information with your tool to refute your partner's claims.
          DO cite your sources.

          DO NOT fabricate fake citations.
          DO NOT cite any source that you did not look up.

          Do not add anything else.

          Stop speaking the moment you finish speaking from your perspective.
          """

agent_system_messages = {name: generate_system_message(name, description) for name, description in agent_descriptions.items()}

# Topic Specification
specified_topic = "The Impact of Remote Work on Employee Productivity"

# Agent Setup
agents = [
    DialogueAgentWithTools(
        name=name,
        system_message=SystemMessage(content=system_message),
        model=ChatOpenAI(model_name="gpt-4", temperature=0.2),
        tool_names= ["arxiv", "ddg-search", "wikipedia"],
        top_k_results=2,
    ) for name, system_message in agent_system_messages.items()
]

# Speaker Selection Function
def select_next_speaker(step, agents):
    return step % len(agents)

# Running the Simulation
max_iters = 4
simulator = DialogueSimulator(agents=agents, selection_function=select_next_speaker)
simulator.reset()
simulator.inject("Moderator", specified_topic)

for _ in range(max_iters):
    name, message = simulator.step()
    print(f"({name}): {message}")





> Entering new AgentExecutor chain...
I believe that remote work can have a negative impact on employee productivity. While it's true that remote work can eliminate commute time and provide a flexible schedule, it can also lead to isolation and a lack of team interaction. This lack of interaction can lead to a decrease in collaboration and innovation, which are key drivers of productivity in many industries. Furthermore, the boundaries between work and personal life can become blurred in a remote work setting, leading to burnout and decreased productivity over time.

```json
{
    "action": "duckduckgo_search",
    "action_input": "impact of remote work on team interaction"
}
```
Observation: Remote work can offer many benefits for your team's engagement, such as increased flexibility, autonomy, productivity, and work-life balance. When employees have more control over their... For starters, one of the biggest challenges associated with remote work is communication. Without the oppor